# IMDB Scraper
using Beautiful soup and selenium to scrape popularity data from IMDB Pro

In [1]:
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from selenium import webdriver
from selenium.webdriver.common.action_chains import ActionChains
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
import datetime
import time
import pickle
from copy import deepcopy

from bs4 import BeautifulSoup
import requests
import string
from concurrent.futures import ThreadPoolExecutor, wait
import warnings
warnings.filterwarnings("ignore")

## Login
In order to use this scrapper you will need a IMDBPro account to login to

In [2]:
def login(driver):
    driver.get("https://pro.imdb.com/login/imdb?u=https%3A%2F%2Fpro.imdb.com%2Fname%2Fnm0000409")
    time.sleep(1)
    driver.find_element(By.ID, 'ap_email').send_keys('your_email')
    driver.find_element(By.ID, 'ap_password').send_keys('your_password')
    driver.find_element(By.ID, 'signInSubmit').click()

In [3]:
# this function returns the titles and urls for every person on the given page
def get_page(page_url, driver):
    driver.get(page_url)
    time.sleep(4)
    names = driver.find_elements(By.TAG_NAME, 'table')
    all_names = []
    for name in names:
        act_name = name.find_element(By.CLASS_NAME, 'a-truncate-cut').text
        act_link = name.find_element(By.CLASS_NAME, 'a-link-normal').get_attribute('href')
        all_names.append((act_name, act_link))
    return all_names

In [190]:
# this gets all of the popularity data for a single person's page
def get_actor(url, driver):
    driver.get(url)
    time.sleep(1.5)
    try:
        driver.find_element(By.ID, 'all').click()
    except:
        return {}
    name = driver.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div/div[2]/div/div[2]/div[1]/div/div[1]/div/div[1]/div/div/div/div[2]/div/h1/span').text
    action = ActionChains(driver)
    highs = pd.DataFrame(columns = ['year', 'score'])
    
    rows = []
    stamps = driver.find_elements(By.TAG_NAME, 'rect')
    for stamp in stamps:
        action.move_to_element(stamp).perform()
        score = driver.find_element(By.CLASS_NAME, 'week_high').text
        date_range = final_driver.find_element(By.ID, 'ranking_graph_container').find_element(By.CLASS_NAME, 'a-row').find_elements(By.TAG_NAME, 'span')[3].text
        day1 = pd.to_datetime(date_range.split(' - ')[0])
        day2 = pd.to_datetime(date_range.split(' - ')[1])
        mid_day = day1.toordinal() + ((day2.toordinal() - day1.toordinal()) / 2)
        year = datetime.date.fromordinal(int(mid_day)).year
        rows.append({'year': year, 'score': int(score.replace(',', ''))})

    for row in rows:
        highs = highs.append(row, ignore_index = True)
    
    final_scores = highs.groupby('year').mean().round()
    return final_scores.score.to_dict()

In [380]:
# this gets the list of all actor urls
page_driver = webdriver.Chrome()
login(page_driver)
time.sleep(5)
master_act_list = []
for num in np.arange(1, 1656):
    url = 'https://pro.imdb.com/discover/people?ref_=hm_nv_ppl_actr&sortOrder=STARMETER_ASC&pageNumber=' + str(num) + '&profession=actor&minNumOfReleasedCredits=2&includeDeceased=true&titleType=movie&starMeterRangeMin=1&starMeterRangeMax=300000'
    act_list = get_page(url, page_driver)
    master_act_list.append(act_list)

In [79]:
# this gets the list of all female actors 
page_driver2 = webdriver.Chrome()
login(page_driver2)
time.sleep(5)
master_fem_act_list = []
for num in np.arange(1, 1111):
    url = 'https://pro.imdb.com/discover/people?profession=actress&ref_=hm_nv_ppl_actrs&starMeterRangeMin=1&sortOrder=RELEVANCE&pageNumber=' + str(num) + '&starMeterRangeMax=300000&minNumOfReleasedCredits=3&includeDeceased=true&titleType=movie'
    act_list = get_page(url, page_driver2)
    master_fem_act_list.append(act_list)

In [81]:
# this reassures that the dataframe is prepared
with open('all_genres_df.pkl', 'rb') as f:
    films_df = pickle.load(f)
    
films = deepcopy(films_df)
films = films.drop_duplicates(subset= ['id'])
films = films[films.release_date != '?']
films = films[films.runtime != 0]
films.release_date = pd.to_datetime(films.release_date)
films.release_date = films.release_date.map(lambda x: x if x.year < 2023 else 2099)
films = films[films.release_date != 2099]
films.release_date = films.release_date.apply(lambda x: x.toordinal())
films = films[films.imdb_rating != 20]
#films.locations = films.locations.map(lambda x: [l.split(',')[-1] for l in x])
films.num_review = films.num_review.apply(lambda x: x*10 if x < 1000 else x)
films = films[films.num_review > 100]
films[['runtime', 'num_review', 'budget']] = films[['runtime', 'num_review', 'imdb_rating']].astype(float)
#films = films[films.budget != 0]
films.dropna(inplace = True)
films.key_words = films.key_words.map(lambda x: [w.lower() for w in x])
films = films.reset_index().drop('index', axis =1)

In [82]:
# this will make sure we only target the actors in the films dataframe
all_act = films.actors.tolist()
actors = []
count = 0
for act_list in all_act:
    for act in act_list:
        if act not in actors:
            actors.append(act)
    count += 1
    print(count)

len(actors)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


2250
2251
2252
2253
2254
2255
2256
2257
2258
2259
2260
2261
2262
2263
2264
2265
2266
2267
2268
2269
2270
2271
2272
2273
2274
2275
2276
2277
2278
2279
2280
2281
2282
2283
2284
2285
2286
2287
2288
2289
2290
2291
2292
2293
2294
2295
2296
2297
2298
2299
2300
2301
2302
2303
2304
2305
2306
2307
2308
2309
2310
2311
2312
2313
2314
2315
2316
2317
2318
2319
2320
2321
2322
2323
2324
2325
2326
2327
2328
2329
2330
2331
2332
2333
2334
2335
2336
2337
2338
2339
2340
2341
2342
2343
2344
2345
2346
2347
2348
2349
2350
2351
2352
2353
2354
2355
2356
2357
2358
2359
2360
2361
2362
2363
2364
2365
2366
2367
2368
2369
2370
2371
2372
2373
2374
2375
2376
2377
2378
2379
2380
2381
2382
2383
2384
2385
2386
2387
2388
2389
2390
2391
2392
2393
2394
2395
2396
2397
2398
2399
2400
2401
2402
2403
2404
2405
2406
2407
2408
2409
2410
2411
2412
2413
2414
2415
2416
2417
2418
2419
2420
2421
2422
2423
2424
2425
2426
2427
2428
2429
2430
2431
2432
2433
2434
2435
2436
2437
2438
2439
2440
2441
2442
2443
2444
2445
2446
2447
2448
2449


3976
3977
3978
3979
3980
3981
3982
3983
3984
3985
3986
3987
3988
3989
3990
3991
3992
3993
3994
3995
3996
3997
3998
3999
4000
4001
4002
4003
4004
4005
4006
4007
4008
4009
4010
4011
4012
4013
4014
4015
4016
4017
4018
4019
4020
4021
4022
4023
4024
4025
4026
4027
4028
4029
4030
4031
4032
4033
4034
4035
4036
4037
4038
4039
4040
4041
4042
4043
4044
4045
4046
4047
4048
4049
4050
4051
4052
4053
4054
4055
4056
4057
4058
4059
4060
4061
4062
4063
4064
4065
4066
4067
4068
4069
4070
4071
4072
4073
4074
4075
4076
4077
4078
4079
4080
4081
4082
4083
4084
4085
4086
4087
4088
4089
4090
4091
4092
4093
4094
4095
4096
4097
4098
4099
4100
4101
4102
4103
4104
4105
4106
4107
4108
4109
4110
4111
4112
4113
4114
4115
4116
4117
4118
4119
4120
4121
4122
4123
4124
4125
4126
4127
4128
4129
4130
4131
4132
4133
4134
4135
4136
4137
4138
4139
4140
4141
4142
4143
4144
4145
4146
4147
4148
4149
4150
4151
4152
4153
4154
4155
4156
4157
4158
4159
4160
4161
4162
4163
4164
4165
4166
4167
4168
4169
4170
4171
4172
4173
4174
4175


5619
5620
5621
5622
5623
5624
5625
5626
5627
5628
5629
5630
5631
5632
5633
5634
5635
5636
5637
5638
5639
5640
5641
5642
5643
5644
5645
5646
5647
5648
5649
5650
5651
5652
5653
5654
5655
5656
5657
5658
5659
5660
5661
5662
5663
5664
5665
5666
5667
5668
5669
5670
5671
5672
5673
5674
5675
5676
5677
5678
5679
5680
5681
5682
5683
5684
5685
5686
5687
5688
5689
5690
5691
5692
5693
5694
5695
5696
5697
5698
5699
5700
5701
5702
5703
5704
5705
5706
5707
5708
5709
5710
5711
5712
5713
5714
5715
5716
5717
5718
5719
5720
5721
5722
5723
5724
5725
5726
5727
5728
5729
5730
5731
5732
5733
5734
5735
5736
5737
5738
5739
5740
5741
5742
5743
5744
5745
5746
5747
5748
5749
5750
5751
5752
5753
5754
5755
5756
5757
5758
5759
5760
5761
5762
5763
5764
5765
5766
5767
5768
5769
5770
5771
5772
5773
5774
5775
5776
5777
5778
5779
5780
5781
5782
5783
5784
5785
5786
5787
5788
5789
5790
5791
5792
5793
5794
5795
5796
5797
5798
5799
5800
5801
5802
5803
5804
5805
5806
5807
5808
5809
5810
5811
5812
5813
5814
5815
5816
5817
5818


7273
7274
7275
7276
7277
7278
7279
7280
7281
7282
7283
7284
7285
7286
7287
7288
7289
7290
7291
7292
7293
7294
7295
7296
7297
7298
7299
7300
7301
7302
7303
7304
7305
7306
7307
7308
7309
7310
7311
7312
7313
7314
7315
7316
7317
7318
7319
7320
7321
7322
7323
7324
7325
7326
7327
7328
7329
7330
7331
7332
7333
7334
7335
7336
7337
7338
7339
7340
7341
7342
7343
7344
7345
7346
7347
7348
7349
7350
7351
7352
7353
7354
7355
7356
7357
7358
7359
7360
7361
7362
7363
7364
7365
7366
7367
7368
7369
7370
7371
7372
7373
7374
7375
7376
7377
7378
7379
7380
7381
7382
7383
7384
7385
7386
7387
7388
7389
7390
7391
7392
7393
7394
7395
7396
7397
7398
7399
7400
7401
7402
7403
7404
7405
7406
7407
7408
7409
7410
7411
7412
7413
7414
7415
7416
7417
7418
7419
7420
7421
7422
7423
7424
7425
7426
7427
7428
7429
7430
7431
7432
7433
7434
7435
7436
7437
7438
7439
7440
7441
7442
7443
7444
7445
7446
7447
7448
7449
7450
7451
7452
7453
7454
7455
7456
7457
7458
7459
7460
7461
7462
7463
7464
7465
7466
7467
7468
7469
7470
7471
7472


...

87879
87880
87881
87882
87883
87884
87885
87886
87887
87888
87889
87890
87891
87892
87893
87894
87895
87896
87897
87898
87899
87900
87901
87902
87903
87904
87905
87906
87907
87908
87909
87910
87911
87912
87913
87914
87915
87916
87917
87918
87919
87920
87921
87922
87923
87924
87925
87926
87927
87928
87929
87930
87931
87932
87933
87934
87935
87936
87937
87938
87939
87940
87941
87942
87943
87944
87945
87946
87947
87948
87949
87950
87951
87952
87953
87954
87955
87956
87957
87958
87959
87960
87961
87962
87963
87964
87965
87966
87967
87968
87969
87970
87971
87972
87973
87974
87975
87976
87977
87978
87979
87980
87981
87982
87983
87984
87985
87986
87987
87988
87989
87990
87991
87992
87993
87994
87995
87996
87997
87998
87999
88000
88001
88002
88003
88004
88005
88006
88007
88008
88009
88010
88011
88012
88013
88014
88015
88016
88017
88018
88019
88020
88021
88022
88023
88024
88025
88026
88027
88028
88029
88030
88031
88032
88033
88034
88035
88036
88037
88038
88039
88040
88041
88042
88043
88044
8804

89245
89246
89247
89248
89249
89250
89251
89252
89253
89254
89255
89256
89257
89258
89259
89260
89261
89262
89263
89264
89265
89266
89267
89268
89269
89270
89271
89272
89273
89274
89275
89276
89277
89278
89279
89280
89281
89282
89283
89284
89285
89286
89287
89288
89289
89290
89291
89292
89293
89294
89295
89296
89297
89298
89299
89300
89301
89302
89303
89304
89305
89306
89307
89308
89309
89310
89311
89312
89313
89314
89315
89316
89317
89318
89319
89320
89321
89322
89323
89324
89325
89326
89327
89328
89329
89330
89331
89332
89333
89334
89335
89336
89337
89338
89339
89340
89341
89342
89343
89344
89345
89346
89347
89348
89349
89350
89351
89352
89353
89354
89355
89356
89357
89358
89359
89360
89361
89362
89363
89364
89365
89366
89367
89368
89369
89370
89371
89372
89373
89374
89375
89376
89377
89378
89379
89380
89381
89382
89383
89384
89385
89386
89387
89388
89389
89390
89391
89392
89393
89394
89395
89396
89397
89398
89399
89400
89401
89402
89403
89404
89405
89406
89407
89408
89409
89410
8941

90616
90617
90618
90619
90620
90621
90622
90623
90624
90625
90626
90627
90628
90629
90630
90631
90632
90633
90634
90635
90636
90637
90638
90639
90640
90641
90642
90643
90644
90645
90646
90647
90648
90649
90650
90651
90652
90653
90654
90655
90656
90657
90658
90659
90660
90661
90662
90663
90664
90665
90666
90667
90668
90669
90670
90671
90672
90673
90674
90675
90676
90677
90678
90679
90680
90681
90682
90683
90684
90685
90686
90687
90688
90689
90690
90691
90692
90693
90694
90695
90696
90697
90698
90699
90700
90701
90702
90703
90704
90705
90706
90707
90708
90709
90710
90711
90712
90713
90714
90715
90716
90717
90718
90719
90720
90721
90722
90723
90724
90725
90726
90727
90728
90729
90730
90731
90732
90733
90734
90735
90736
90737
90738
90739
90740
90741
90742
90743
90744
90745
90746
90747
90748
90749
90750
90751
90752
90753
90754
90755
90756
90757
90758
90759
90760
90761
90762
90763
90764
90765
90766
90767
90768
90769
90770
90771
90772
90773
90774
90775
90776
90777
90778
90779
90780
90781
9078

92014
92015
92016
92017
92018
92019
92020
92021
92022
92023
92024
92025
92026
92027
92028
92029
92030
92031
92032
92033
92034
92035
92036
92037
92038
92039
92040
92041
92042
92043
92044
92045
92046
92047
92048
92049
92050
92051
92052
92053
92054
92055
92056
92057
92058
92059
92060
92061
92062
92063
92064
92065
92066
92067
92068
92069
92070
92071
92072
92073
92074
92075
92076
92077
92078
92079
92080
92081
92082
92083
92084
92085
92086
92087
92088
92089
92090
92091
92092
92093
92094
92095
92096
92097
92098
92099
92100
92101
92102
92103
92104
92105
92106
92107
92108
92109
92110
92111
92112
92113
92114
92115
92116
92117
92118
92119
92120
92121
92122
92123
92124
92125
92126
92127
92128
92129
92130
92131
92132
92133
92134
92135
92136
92137
92138
92139
92140
92141
92142
92143
92144
92145
92146
92147
92148
92149
92150
92151
92152
92153
92154
92155
92156
92157
92158
92159
92160
92161
92162
92163
92164
92165
92166
92167
92168
92169
92170
92171
92172
92173
92174
92175
92176
92177
92178
92179
9218

329422

In [83]:
# this will make sure we only target the director in the films dataframe
all_dir = films.director.tolist()
directors = []
count = 0
for dir_list in all_dir:
    for direct in dir_list:
        if direct not in directors:
            directors.append(direct)
    count += 1
    print(count, end = '\r')

len(directors)

39541

In [86]:
# this will make sure we only target the writers in the films dataframe
all_writ = films.writer.tolist()
writers = []
count = 0
for writ_list in all_writ:
    for writ in writ_list:
        if writ not in writers:
            writers.append(writ)
    count += 1
    print(count, end = '\r')

len(writers)

82005

In [195]:
# this will make sure we only target the female actors in the films dataframe
all_comp = films.prod_comp.tolist()
comps = []
count = 0
for comp_list in all_comp:
    for comp in comp_list:
        if comp not in comps:
            comps.append(comp)
    count += 1
    print(count, end = '\r')

len(comps)

46804

In [133]:
actor_urls = {}
for a_list in master_act_list:
    for a in a_list:
        full_name = a[0] + ' ' + a[1].split('name/nm')[-1].split("?ref")[0]
        if full_name in actors:
            actor_urls[full_name] = a[1]
    print(len(actor_urls), end = '\r')

NameError: name 'master_act_list' is not defined

In [128]:
fem_actor_urls = {}
for a_list in master_fem_act_list:
    for a in a_list:
        full_name = a[0] + ' ' + a[1].split('name/nm')[-1].split("?ref")[0]
        if full_name in actors:
            fem_actor_urls[full_name] = a[1]
    print(len(fem_actor_urls), end = '\r')

In [155]:
with open('mdl.pkl', 'rb') as f:
    master_dir_list = pickle.load(f)

with open('mwl.pkl', 'rb') as f:
    master_write_list = pickle.load(f)

In [162]:
write_dir_urls = {}
for dir_list in master_dir_list:
    for direct in dir_list:
        full_name = direct[0] + ' ' + direct[1].split('name/nm')[-1].split("?ref")[0]
        if full_name in directors:
            write_dir_urls[full_name] = direct[1]
    print(len(write_dir_urls), end = '\r')

for writ_list in master_write_list:
    for writ in writ_list:
        full_name = writ[0] + ' ' + writ[1].split('name/nm')[-1].split("?ref")[0]
        if (full_name in writers) & (full_name not in list(write_dir_urls.keys())):
            write_dir_urls[full_name] = writ[1]
    print(len(write_dir_urls), end = '\r')

done6


In [ ]:
actor_urls = actor_urls | fem_actor_urls

In [169]:
with open('actor_urls.pkl', 'wb') as f:
    pickle.dump(actor_urls, f)
with open('write_dir_urls.pkl', 'wb') as f:
    pickle.dump(write_dir_urls, f)
with open('fem_urls.pkl', 'wb') as f:
    pickle.dump(fem_actor_urls, f)

In [188]:
len(write_dir_urls)

20307

In [199]:
len(wd_pop_dict)

1692

In [192]:
final_driver = webdriver.Chrome()
final_driver.get('https://pro.imdb.com/login/ap?u=/login/lwa&imdbPageAction=signUp&rf=cons_nb_hm&ref_=cons_nb_hm')
time.sleep(40)

all_names = list(write_dir_urls.items())
wd_pop_dict = {}

for act in all_names[7:1692]:
    name = act[0]
    url = act[1]
    wd_pop_dict[name] = get_actor(url, final_driver)
    
with open('wd_pop_1.pkl', 'wb') as f:
    pickle.dump(wd_pop_dict, f)

# for act in all_names[1692:3384]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_2.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[3384:5076]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_3.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[5076:6768]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_4.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[6768:8460]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_5.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[8460:10152]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_6.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[10152:11844]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_7.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[11844:13536]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_8.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[13536:15228]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_9.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[15228:16920]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_10.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[16920:18612]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_11.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)

# for act in all_names[18612:]:
#     name = act[0]
#     url = act[1]
#     wd_pop_dict[name] = get_actor(url, final_driver)
    
# with open('wd_pop_12.pkl', 'wb') as f:
#     pickle.dump(wd_pop_dict, f)



In [ ]:
# final_driver = webdriver.Chrome()
# login(final_driver)
# time.sleep(25)

# all_names = list(actor_urls.items())
#actor_pop_dict = {}

# for act in all_names[:10000]:
#     name = act[0]
#     url = act[1]
#     actor_pop_dict[name] = get_actor(url, final_driver)

In [200]:
with open('wd_pop_1.pkl', 'wb') as f:
    pickle.dump(wd_pop_dict, f)

{'James Cameron 0000116': {1997: 17.0,
  1998: 46.0,
  1999: 149.0,
  2000: 144.0,
  2001: 247.0,
  2002: 300.0,
  2003: 271.0,
  2004: 441.0,
  2005: 485.0,
  2006: 428.0,
  2007: 415.0,
  2008: 558.0,
  2009: 72.0,
  2010: 122.0,
  2011: 252.0,
  2012: 159.0,
  2013: 588.0,
  2014: 691.0,
  2015: 532.0,
  2016: 559.0,
  2017: 318.0,
  2018: 492.0,
  2019: 200.0,
  2020: 856.0,
  2021: 701.0,
  2022: 141.0},
 'Peter Billingsley 0082526': {1997: 2666.0,
  1998: 1315.0,
  1999: 1030.0,
  2000: 917.0,
  2001: 768.0,
  2002: 1729.0,
  2003: 1983.0,
  2004: 1774.0,
  2005: 1339.0,
  2006: 305.0,
  2007: 995.0,
  2008: 636.0,
  2009: 334.0,
  2010: 1238.0,
  2011: 1627.0,
  2012: 2202.0,
  2013: 1761.0,
  2014: 2168.0,
  2015: 2360.0,
  2016: 1698.0,
  2017: 2568.0,
  2018: 4160.0,
  2019: 1028.0,
  2020: 1257.0,
  2021: 2108.0,
  2022: 1691.0},
 'Christopher Nolan 0634240': {1998: 29760.0,
  1999: 10257.0,
  2000: 6363.0,
  2001: 258.0,
  2002: 210.0,
  2003: 271.0,
  2004: 530.0,
  2005: 